In [1]:
import os
import sys
import torch
import transformers
import tqdm
import random
import json
import matplotlib.pyplot as plt
import scipy
import logging
from collections import defaultdict
from transformers import AutoModel, AutoTokenizer, AutoModelForCausalLM, GPTNeoXTokenizerFast, GPTNeoXForCausalLM
from surprisal import AutoHuggingFaceModel, KenLMModel


In [2]:
FILE = "/Users/simonchervenak/Documents/GitHub/flexiprisal/sud-treebanks-v2.15/SUD_English-Atis/en_atis-sud-train.conllu"

In [3]:
columns = "ID FORM LEMMA UPOS XPOS FEATS HEAD DEPREL DEPS MISC".split()

In [4]:
logger = logging.getLogger()
fhandler = logging.FileHandler(filename='output-subj.log', mode='a')
formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
fhandler.setFormatter(formatter)
logger.addHandler(fhandler)
logger.setLevel(logging.DEBUG)

In [5]:
def calculate_surprisal(model_variant, mode, language, dep_type):
    stories = generate_stories(language, dep_type)
    try:
        try:
            tokenizer = AutoTokenizer.from_pretrained(model_variant, use_fast=False)#, from_flax=True)
            model = AutoModelForCausalLM.from_pretrained(model_variant)#, from_flax=True)
        except Exception as e:
            tokenizer = AutoTokenizer.from_pretrained(model_variant, use_fast=False, from_tf=True)
            model = AutoModelForCausalLM.from_pretrained(model_variant, from_tf=True)
    except Exception as e:
        tokenizer = AutoTokenizer.from_pretrained(model_variant, use_fast=False, from_flax=True)
        model = AutoModelForCausalLM.from_pretrained(model_variant, from_flax=True)

    model.eval()
    softmax = torch.nn.Softmax(dim=-1)
    ctx_size = model.config.max_position_embeddings
    bos_id = model.config.bos_token_id

    batches = []
    words = []
    vocab_size = model.config.vocab_size
    for story in tqdm.tqdm(stories):#, position=1):
        words.extend(story.split(" "))
        tokenizer_output = tokenizer(story)
        ids = tokenizer_output.input_ids
        ids = [id_val if id_val < vocab_size else tokenizer.unk_token_id for id_val in ids]
        attn = tokenizer_output.attention_mask

        # these tokenizers do not append bos_id by default
        if "gpt" in model_variant or "pythia" in model_variant:
            ids = [bos_id] + ids
            attn = [1] + attn

        start_idx = 0

        # sliding windows with 50% overlap
        # start_idx is for correctly indexing the "later 50%" of sliding windows
        while len(ids) > ctx_size:
            # for models that explicitly require the first dimension (batch_size)
            if "gpt-neox" in model_variant or "pythia" in model_variant or "opt" in model_variant:
                batches.append((transformers.BatchEncoding({"input_ids": torch.tensor(ids[:ctx_size]).unsqueeze(0),
                                                            "attention_mask": torch.tensor(attn[:ctx_size]).unsqueeze(0)}),
                                torch.tensor(ids[1:ctx_size+1]), start_idx, True))
            # for other models
            else: #elif "gpt" in model_variant:
                batches.append((transformers.BatchEncoding({"input_ids": torch.tensor(ids[:ctx_size]),
                                                            "attention_mask": torch.tensor(attn[:ctx_size])}),
                                torch.tensor(ids[1:ctx_size+1]), start_idx, True))

            ids = ids[int(ctx_size/2):]
            attn = attn[int(ctx_size/2):]
            start_idx = int(ctx_size/2)

        # remaining tokens
        if "gpt-neox" in model_variant or "pythia" in model_variant or "opt" in model_variant:
            batches.append((transformers.BatchEncoding({"input_ids": torch.tensor(ids[:-1]).unsqueeze(0),
                                                        "attention_mask": torch.tensor(attn[:-1]).unsqueeze(0)}),
                           torch.tensor(ids[1:]), start_idx, False))
        else: #elif "gpt" in model_variant:
            batches.append((transformers.BatchEncoding({"input_ids": torch.tensor(ids[:-1]),
                                                        "attention_mask": torch.tensor(attn[:-1])}),
                           torch.tensor(ids[1:]), start_idx, False))

    print("word llmsurp")
    
    curr_word_surp = []
    curr_toks = []
    curr_word_ix = 0
    is_continued = False
    count = 0
    total = 0
    for batch in tqdm.tqdm(random.sample(batches, min(1000, len(batches)))):#, position=1):
        try:
            # print("reading", batch)
            batch_input, output_ids, start_idx, will_continue = batch
    
            with torch.no_grad():
                model_output = model(**batch_input)
    
            toks = tokenizer.convert_ids_to_tokens(output_ids)
            index = torch.arange(0, output_ids.shape[0])
            surp = -1 * torch.log2(softmax(model_output.logits).squeeze(0)[index, output_ids])
    
            if mode == "token":
                # token-level surprisal
                # for i in range(start_idx, len(toks)):
                #     cleaned_tok = tokenizer.convert_tokens_to_string([toks[i]]).replace(" ", "")
                #     # print(cleaned_tok, surp[i].item())
                #     if total > 250:
                #         continue
                #     total += surp[i].item()
                #     count += 1
                #     # print(count, total)
                total += surp[-1].item()
                count += 1
    
            elif mode == "word":
                # word-level surprisal
                # if the batch starts a new story
                if not is_continued:
                    curr_word_surp = []
                    curr_toks = []
                for i in range(start_idx, len(toks)):
                    curr_word_surp.append(surp[i].item())
                    curr_toks += [toks[i]]
                    curr_toks_str = tokenizer.convert_tokens_to_string(curr_toks)
                    # summing token-level surprisal
                    # print(words[curr_word_ix], curr_toks_str.strip())
                    if words[curr_word_ix] == curr_toks_str.strip():
                        # print(curr_toks_str.strip(), sum(curr_word_surp))
                        count += 1
                        total += sum(curr_word_surp)
                        curr_word_surp = []
                        curr_toks = []
                        curr_word_ix += 1
                        # print(count, total)
    
            is_continued = will_continue
    
            del model_output
        except Exception as e:
            print("error reading batch", tokenizer.convert_tokens_to_string(tokenizer.convert_ids_to_tokens(output_ids)))
    # print(count, total)
    return total / count

# calculate_surprisal("surajp/gpt2-hindi", "token", "Hindi")
    

In [6]:
def read_conllu(file):
    conllu = []
    with open(file) as f:
        stories = f.read().split("\n\n")[:-1]
        # print(file, columns)
        for story in stories:
            # print(story)
            # input()
            rows = story.strip().split("\n")
            rows = [i for i in rows if not i.startswith("#")]
            table = [dict(zip(columns, row.split())) for row in rows]
            conllu.append(table)
    return conllu

def generate_examples(conllu, dep_type):
    examples = []
    for story in conllu:
        target = None
        example = ""
        # print(story)
        for word in story:
            # print(word)
            example += word['FORM'] + ' '
            if word['DEPREL'] == dep_type:
                if int(word['HEAD']) < int(word['ID']):
                    break
                else:
                    target = word['HEAD']
            elif word['ID'] == target:
                break
        examples.append(example.strip())
    return examples

def generate_stories(language, dep_type):
    stories = []
    for a, b, c in os.walk('ud-215/ud-treebanks-v2.15'):
        if language in a:
            for f in c:
                if any(map(lambda i: f.endswith(i), ['dev.conllu', 'test.conllu', 'train.conllu'])):
                    conllu = read_conllu(f'{a}/{f}')
                    examples = generate_examples(conllu, dep_type)
                    stories.extend(examples)
    return stories

In [7]:
def surprisal_by_dep_type(language, model_variant):
    stories = []
    for a, b, c in os.walk('ud-215/ud-treebanks-v2.15'):
        if language in a:
            for f in c:
                if any(map(lambda i: f.endswith(i), ['dev.conllu', 'test.conllu', 'train.conllu'])):
                    conllu = read_conllu(f'{a}/{f}')
                    stories.extend(conllu)

    try:
        try:
            model = AutoHuggingFaceModel.from_pretrained(model_variant)#, from_flax=True)
        except Exception as e:
            model = AutoHuggingFaceModel.from_pretrained(model_variant, from_tf=True)
    except Exception as e:
        model = AutoHuggingFaceModel.from_pretrained(model_variant, from_flax=True)

    values = defaultdict(list)

    try:
        for conllu in tqdm.tqdm(stories[:5000]):
            sent = ' '.join(i['FORM'] for i in conllu)
            # print(sent, conllu)
            for k, result in enumerate(model.surprise(sent)[0]):
                # print(k, result)
                # tok = conllu[k]
                tok = [i for i in conllu if i['FORM'] in result[0]]
                if tok:
                    values[tok[0]['DEPREL']].append(float(result[1]))
    except KeyboardInterrupt:
        ...

    # print(values)
    averages = {}
    for k, v in values.items():
        averages[k] = sum(v) / len(v)
    return averages
        # print(conllu, ' '.join(i['FORM'] for i in conllu))
        # input()

# models = {i.split(":")[0]: i.split(":")[1] for i in open("models.txt").read().split("\n")[:-1]}

# surprisal_by_dep_type("English", models["English"])

In [47]:
# model = AutoHuggingFaceModel.from_pretrained(models['English'])
# for k in model.surprise("I told the cat")[0]:
#     print(k)
#     print(float(k[1]))

In [ ]:
models = {i.split(":")[0]: i.split(":")[1] for i in open("models.txt").read().split("\n")[:-1]}

# surprisals = {}

for lang in tqdm.tqdm(list(models.keys())[12:]):
    model = models[lang]
    logger.info(f"starting {lang}")
    try:
        # token_surprisal = calculate_surprisal(model, "token", lang, "subj")
        surprisal_averages = surprisal_by_dep_type(lang, model)
        # surprisals[lang] = token_surprisal

        for k, v in surprisal_averages.items():
            with open(f"surprisals-avg{k}-1-{lang}.txt", "w") as f:
                f.write(f"Token: {v}\n")
        
        logger.info(f"finished {lang}")
    except Exception as e:
        logger.error(f"ERROR ON LANG {lang}")
        logger.error(f"[-] {e}")

 28%|███████████▊                               | 8/29 [20:16<55:28, 158.52s/it]You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565

 91%|███████████████████████████████████▍   | 4538/5000 [34:50<03:13,  2.38it/s]

 71%|███████████████████████████▋           | 3542/5000 [01:55<00:40, 35.84it/s]

 25%|██████████▏                             | 668/2625 [02:12<06:26,  5.07it/s]

 45%|█████████████████▍                     | 1750/3905 [05:00<06:22,  5.63it/s]

 97%|█████████████████████████████████████▋ | 3779/3905 [10:45<00:19,  6.48it/s]

In [7]:
models = {i.split(":")[0]: i.split(":")[1] for i in open("models.txt").read().split("\n")[:-1]}

surprisals = {}

for lang in tqdm.tqdm(list(models.keys())):
    model = models[lang]
    logger.info(f"starting {lang}")
    try:
        token_surprisal = calculate_surprisal(model, "token", lang, "subj")
        surprisals[lang] = token_surprisal
        
        with open(f"surprisals-subj-2-{lang}.txt", "w") as f:
            f.write(f"Token: {token_surprisal}\n")
        
        logger.info(f"finished {lang}")
    except Exception as e:
        logger.error(f"ERROR ON LANG {lang}")
        logger.error(f"[-] {e}")

100%|███████████████████████████████████| 29789/29789 [00:04<00:00, 6715.08it/s]


word llmsurp



  0%|                                                  | 0/8993 [00:00<?, ?it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (53 > 50). Running this sequence through the model will result in indexing errors

100%|█████████████████████████████████████| 8993/8993 [00:01<00:00, 7649.67it/s]


word llmsurp



100%|███████████████████████████████████| 25231/25231 [00:04<00:00, 5950.30it/s]


...

word llmsurp



 98%|█████████████████████████████████████████▉ | 40/41 [40:11<01:01, 61.55s/it]If you want to use `RobertaLMHeadModel` as a standalone, add `is_decoder=True.`

100%|███████████████████████████████████| 53564/53564 [00:06<00:00, 8173.49it/s]


word llmsurp



100%|███████████████████████████████████████████| 41/41 [40:20<00:00, 59.03s/it]

error reading batch Var þá prófastur síra Stephán Einarsson ei heima , ektamaður madame Jórunnar .</s>
error reading batch Næsti leikur er á heimavelli Gróttu á Seltjarnarnesi og því er útlitið dökkt fyrir Framkonur .</s>
error reading batch Gengu allir fyrirmenn þessa lands til þeirrar stóru búðar , sem upp var reist í Öxarárhólma , hvar hirðstjórabúðin stóð fyrrum .</s>
error reading batch Ef eitthvað var ágerðist sársaukinn enn , uns hann jaðraði við þjáningar , og um leið tók hann að breytast .</s>
error reading batch Ég segi honum það .</s>
error reading batch Eggjar nú Sveinn konungur menn sína og biður þá minnast hversu margt illt þeir Haraldur konungur hafa gert í þeira ríki og hversu þungt er að liggja undir þeira ófriði og miklum óveg , " og látum það spyrjast að vér gangim vel fram og drengiliga .</s>
error reading batch Þar af sjáum vær að þær klaga oss fyrir réttlætisdómstóli Guðs lifanda .</s>
error reading batch Enn er ekkert lát á rannsóknum og leiðöngrum til eyjunnar .

In [8]:
models = {i.split(":")[0]: i.split(":")[1] for i in open("models.txt").read().split("\n")[:-1]}

surprisals = {}

for lang in tqdm.tqdm(list(models.keys())):
    model = models[lang]
    logger.info(f"starting {lang}")
    try:
        token_surprisal = calculate_surprisal(model, "token", lang, "mod")
        surprisals[lang] = token_surprisal
        
        with open(f"surprisals-mod-1-{lang}.txt", "w") as f:
            f.write(f"Token: {token_surprisal}\n")
        
        logger.info(f"finished {lang}")
    except Exception as e:
        logger.error(f"ERROR ON LANG {lang}")
        logger.error(f"[-] {e}")

100%|███████████████████████████████████| 29789/29789 [00:04<00:00, 7099.19it/s]


word llmsurp



  0%|                                                  | 0/8993 [00:00<?, ?it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (53 > 50). Running this sequence through the model will result in indexing errors

100%|█████████████████████████████████████| 8993/8993 [00:00<00:00, 9298.91it/s]


word llmsurp



100%|███████████████████████████████████| 25231/25231 [00:04<00:00, 6265.60it/s]


...

word llmsurp



 98%|█████████████████████████████████████████▉ | 40/41 [39:42<01:04, 64.26s/it]If you want to use `RobertaLMHeadModel` as a standalone, add `is_decoder=True.`

100%|███████████████████████████████████| 53564/53564 [00:06<00:00, 8315.95it/s]


word llmsurp



100%|███████████████████████████████████████████| 41/41 [39:50<00:00, 58.31s/it]

error reading batch Frelsa þú mig af þeim helvíska úlfi .</s>
error reading batch Starfsfólki stofnananna var kynnt greining á sameiningunni í dag og segja stjórnendur hjá Minjastofnun ýmislegt í þeirri greiningu mögulega rangt .</s>
error reading batch Þórarinn sótti að Þorkatli og tveir menn með honum .</s>
error reading batch Þetta gerir ekkert til , blessuð börnin þurfa að leika sér " .</s>
error reading batch Fljótlega upp úr því var hafist handa við að kortleggja sérstaklega vanda þessa hóps , safna um það upplýsingum og hefja síðan viðræður við lífeyrissjóðina .</s>
error reading batch Vegagerðin áætlar að hefla Meðallandsveg en ekki fyrr en í næstu viku .</s>
error reading batch Hann var rammíslenzkur hátt og lágt , svipfríður og reisulegur , með mörg stafnþil fram að hlaðinu .</s>
error reading batch Agis kóngur Lacedarmonior lét brenna alla okurkarla og allan þeirra reikning og ábata .</s>
error reading batch Anno 1682 var auglýst kongl. Majst gefið þann 25. Aprilis sama ár ,

In [9]:
models = {i.split(":")[0]: i.split(":")[1] for i in open("models.txt").read().split("\n")[:-1]}

surprisals = {}

for lang in tqdm.tqdm(list(models.keys())):
    model = models[lang]
    logger.info(f"starting {lang}")
    try:
        token_surprisal = calculate_surprisal(model, "token", lang, "comp")
        surprisals[lang] = token_surprisal
        
        with open(f"surprisals-comp-1-{lang}.txt", "w") as f:
            f.write(f"Token: {token_surprisal}\n")
        
        logger.info(f"finished {lang}")
    except Exception as e:
        logger.error(f"ERROR ON LANG {lang}")
        logger.error(f"[-] {e}")

100%|███████████████████████████████████| 29789/29789 [00:04<00:00, 6935.42it/s]


word llmsurp



  0%|                                                  | 0/8993 [00:00<?, ?it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (53 > 50). Running this sequence through the model will result in indexing errors

100%|█████████████████████████████████████| 8993/8993 [00:01<00:00, 8989.16it/s]


word llmsurp



100%|███████████████████████████████████| 25231/25231 [00:04<00:00, 6155.27it/s]


...

word llmsurp



 98%|█████████████████████████████████████████▉ | 40/41 [41:16<01:06, 66.85s/it]If you want to use `RobertaLMHeadModel` as a standalone, add `is_decoder=True.`

100%|███████████████████████████████████| 53564/53564 [00:06<00:00, 8206.04it/s]


word llmsurp



100%|███████████████████████████████████████████| 41/41 [41:24<00:00, 60.60s/it]

error reading batch Þá skal skjótt kjörið gera að eg kýs yðra dóttur mér til unnustu " , kallandi hana bestan grip í hans eigu .</s>
error reading batch Lést þar þá margt manna en fjöldi varð sár áður Sturla veitti atkvæði að hætta skyldi áverkum við menn .</s>
error reading batch Þá komu þeir Svarthöfði sunnan .</s>
error reading batch Grettir kjöri að fara til þings og svo var að hann fór .</s>
error reading batch Og einkis spurðu þeir hana og létu hana fara og mæltu : " Guð feðra vorra gefi þér giftu og efli öll ráð hjarta þíns af sínum krafti , að Jerúsalem dýrkist yfir þér og sé nafn þitt í tölu heilagra og réttlátra . "</s>
error reading batch Síðan stígur hann á bak sínum hesti og ríður heim að borginni .</s>
error reading batch Ef þeir hafa vald yfir mér , frændur mínir , þá hygg eg að mér sé dauðinn einn ætlaður en það veit guð með mér þó að eg eigi vald á þeim að engis þeirra blóði skal eg út hella . "</s>
error reading batch Hversu mikið af lífi mínu er þannig farið forgörðu